In [1]:
import pandas as pd
from geopy.distance import distance
from config_bd import get_connection
from credenciales_sqlserver import *

In [2]:
completo = pd.read_csv('transform_listings.csv')

In [3]:
completo.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 13871 entries, 0 to 13870
Data columns (total 23 columns):
 #   Column                        Non-Null Count  Dtype  
---  ------                        --------------  -----  
 0   property_id                   13871 non-null  int64  
 1   listing_url                   13871 non-null  object 
 2   name                          13871 non-null  object 
 3   description                   13510 non-null  object 
 4   neighbourhood_cleansed        13871 non-null  object 
 5   neighbourhood_group_cleansed  13871 non-null  object 
 6   latitude                      13871 non-null  float64
 7   longitude                     13871 non-null  float64
 8   property_type                 13871 non-null  object 
 9   room_type                     13871 non-null  object 
 10  accommodates                  13871 non-null  int64  
 11  bathrooms                     13871 non-null  int64  
 12  bedrooms                      13871 non-null  int64  
 13  a

In [4]:
with get_connection() as conn:
    query = """
    SELECT * FROM TRANSPORTS
    """
    stops = pd.read_sql(query, conn)
    

C:\Users\dsantamaria\AppData\Local\Temp\ipykernel_38256\720485261.py:5: UserWarning: pandas only supports SQLAlchemy connectable (engine/connection) or database string URI or sqlite3 DBAPI2 connection. Other DBAPI2 objects are not tested. Please consider using SQLAlchemy.
  stops = pd.read_sql(query, conn)


In [5]:
stops

id  mode                            stop_name  \
0       1423     4                    PLAZA DE CASTILLA   
1       1424     4                             TRIBUNAL   
2       1425     4                             GRAN VIA   
3       1426     4                                  SOL   
4       1427     4                      TIRSO DE MOLINA   
...      ...   ...                                  ...   
13648  15071    10                 ESTRELLA POLAR NORTE   
13649  15072    10                   ESTRELLA POLAR SUR   
13650  15073    10                        JAIME I NORTE   
13651  15074    10                          JAIME I SUR   
13652  15075    10  POLIGONO INDUSTRIAL CIUDAD DE PARLA   

                          stop_desc       lat      lon  
0        Paseo de la Castellana 189  40.46690 -3.68917  
1            Calle de Fuencarral 81  40.42619 -3.70110  
2               Calle   Gran Vía 23  40.42001 -3.70180  
3      Plaza de la Puerta del Sol 6  40.41688 -3.70326  
4        Plaza de Tirso de Molina 7  40.41235 -3.70466  
...                             ...       ...      ...  
13648      Avda de las Estrellas 14  40.23015 -3.75112  
13649        Avda de los Planetas 9  40.23072 -3.75383  
13650       Avda de las Estrellas 2  40.23414 -3.74969  
13651        Avda de los Planetas 6  40.23470 -3.75240  
13652             Calle   Berlín 61  40.23867 -3.75045  

[13653 rows x 6 columns]

In [6]:
TIPOS_TRANSPORTE = [4,5,6,8,10] #El 9 está integrado en el 8

In [7]:
def calcular_distancias_vivienda(row_viv):
    resultados = {}
    
    for modo in TIPOS_TRANSPORTE:
        paradas_tipo = stops[stops['mode'] == modo]

        if paradas_tipo.empty:
            resultados[f'distancia_mode_{modo}'] = None
            continue

        # filtrar primero por lat/lon cercanas para acelerar

        delta = 0.01
        paradas_candidatas = paradas_tipo[
            (abs(paradas_tipo['lat'] - row_viv['latitude']) < delta) &
            (abs(paradas_tipo['lon'] - row_viv['longitude']) < delta)
        ]




        """ Para mejorar el rendimiento voy iterando incrementando el delta a comprobar, tengo que 
        asegurarme de que haya al menos una parada en el dataset porque sino morimos en el while"""
        while paradas_candidatas.empty:  
            delta += 0.01
            print(f"Buscando paradas cercanas al modo {modo} con delta {delta}")
            paradas_candidatas = paradas_tipo[
                (abs(paradas_tipo['lat'] - row_viv['latitude']) < delta) &
                (abs(paradas_tipo['lon'] - row_viv['longitude']) < delta)
            ]
      

        # if paradas_candidatas.empty:
        #     paradas_candidatas = paradas_tipo  # fallback a todas

        distancias = paradas_candidatas.apply(
            lambda stop: distance(
                (row_viv['latitude'], row_viv['longitude']),
                (stop['lat'], stop['lon'])
            ).meters,
            axis=1
        )

        resultados[f'distancia_mode_{modo}'] = distancias.min()

    return pd.Series(resultados)



In [8]:
new_bnb_dataset = completo.apply(calcular_distancias_vivienda, axis=1)
df = pd.concat([completo, new_bnb_dataset], axis=1)
df

Buscando paradas cercanas al modo 10 con delta 0.02
Buscando paradas cercanas al modo 10 con delta 0.03
Buscando paradas cercanas al modo 10 con delta 0.04
Buscando paradas cercanas al modo 10 con delta 0.05
Buscando paradas cercanas al modo 10 con delta 0.060000000000000005
Buscando paradas cercanas al modo 8 con delta 0.02
Buscando paradas cercanas al modo 10 con delta 0.02
Buscando paradas cercanas al modo 10 con delta 0.03
Buscando paradas cercanas al modo 10 con delta 0.04
Buscando paradas cercanas al modo 10 con delta 0.05
Buscando paradas cercanas al modo 10 con delta 0.060000000000000005
Buscando paradas cercanas al modo 8 con delta 0.02
Buscando paradas cercanas al modo 10 con delta 0.02
Buscando paradas cercanas al modo 10 con delta 0.03
Buscando paradas cercanas al modo 10 con delta 0.04
Buscando paradas cercanas al modo 10 con delta 0.05
Buscando paradas cercanas al modo 10 con delta 0.060000000000000005
Buscando paradas cercanas al modo 10 con delta 0.07
Buscando paradas c

property_id                                       listing_url  \
0                    70059                https://www.airbnb.com/rooms/70059   
1                    70310                https://www.airbnb.com/rooms/70310   
2                    72150                https://www.airbnb.com/rooms/72150   
3                    84719                https://www.airbnb.com/rooms/84719   
4                    86042                https://www.airbnb.com/rooms/86042   
...                    ...                                               ...   
13866  1368974630547284843  https://www.airbnb.com/rooms/1368974630547284843   
13867  1368981094706864086  https://www.airbnb.com/rooms/1368981094706864086   
13868  1368985680426539467  https://www.airbnb.com/rooms/1368985680426539467   
13869  1368986418960986344  https://www.airbnb.com/rooms/1368986418960986344   
13870  1368991577357063431  https://www.airbnb.com/rooms/1368991577357063431   

                                                    name  \
0                          Tu hogar en centro de Madrid.   
1        Heart of Malasaña Cozy, Quiet & Sunny Apartment   
2       Sunny attic duplex flat with terrace next to Sol   
3                      Cool Apart. (10min Center + WIFI)   
4      Cozy attic with intimate rooftop terrace+ elev...   
...                                                  ...   
13866                         Coqueto estudio en tetuan!   
13867                          Bonito estudio en Tetuán!   
13868        Acogedor y nuevo ático con gran terraza (B)   
13869                    Elegante apartamento en Madrid!   
13870                          Tropical apartment Madrid   

                                             description  \
0      Very nice, cozy and bright, right in the cente...   
1      Cozy Apartment in great location in the center...   
2      Nestled in the serene heart of Madrid, this re...   
3      Cool and confortable 1 bedroom apartment for 2...   
4      Nestled in Madrid's tranquil heart, this apart...   
...                                                  ...   
13866  Disconnect from the routine in this charming a...   
13867  Get away from routine at this unique and relax...   
13868  Cozy penthouse floor with large terrace, locat...   
13869  Have fun with the whole family at this stylish...   
13870  Get away from routine at this unique and relax...   

      neighbourhood_cleansed neighbourhood_group_cleansed   latitude  \
0                Universidad                       Centro  40.423810   
1                Universidad                       Centro  40.422520   
2                Embajadores                       Centro  40.411500   
3                Embajadores                       Centro  40.408660   
4                Embajadores                       Centro  40.409390   
...                      ...                          ...        ...   
13866          Valdeacederas                       Tetuán  40.464951   
13867          Valdeacederas                       Tetuán  40.468355   
13868               Canillas                    Hortaleza  40.464110   
13869             San Isidro                  Carabanchel  40.395983   
13870             San Isidro                  Carabanchel  40.395621   

       longitude       property_type        room_type  ...  \
0      -3.710380  Entire rental unit  Entire home/apt  ...   
1      -3.702500  Entire rental unit  Entire home/apt  ...   
2      -3.704490  Entire rental unit  Entire home/apt  ...   
3      -3.703740  Entire rental unit  Entire home/apt  ...   
4      -3.698120  Entire rental unit  Entire home/apt  ...   
...          ...                 ...              ...  ...   
13866  -3.704578  Entire rental unit  Entire home/apt  ...   
13867  -3.706939  Entire rental unit  Entire home/apt  ...   
13868  -3.647130  Entire rental unit  Entire home/apt  ...   
13869  -3.730953  Entire rental unit  Entire home/apt  ...   
13870  -3.731533  Entire rental unit  Entire home/apt  ...   

  

In [ ]:
df.rename(columns={
    'distancia_mode_4': 'DISTANCE_TO_METRO',
    'distancia_mode_5': 'DISTANCE_TO_CERCANIAS',
    'distancia_mode_6': 'DISTANCE_TO_EMT',
    'distancia_mode_8': 'DISTANCE_TO_INTERURBANOS',
    'distancia_mode_10': 'DISTANCE_TO_MLO'
}, inplace=True)


df.to_csv('transform_listings_con_distancias_red_transporte.csv', index=False)